# Load Modules

In [72]:
import pickle
from sentence_transformers import SentenceTransformer, util
import subprocess
import torch
from getPassageFromPID import DocContentManager
from sklearn.neighbors import NearestNeighbors
from sklearn.metrics.pairwise import cosine_similarity
from keybert import KeyBERT
import sys
sentence_transformer_model = SentenceTransformer('all-MiniLM-L6-v2')
kw_model = KeyBERT(model='all-MiniLM-L6-v2')


combined_corpus_embeddings_path = "combined_corpus_embeddings/combined_corpus_embeddings"
queries_path = 'validation/msmarco-test2019-queries.tsv'
top100_path = 'validation/msmarco-passagetest2019-top1000.tsv'
qrels_path = 'validation/2019qrels-pass.txt'

# Load Embeddings

In [62]:
with open(combined_corpus_embeddings_path, 'rb') as file:
    corpus_embeddings = pickle.load(file)

In [63]:
corpus_embeddings = torch.tensor(corpus_embeddings)

C:\Users\asg41\AppData\Local\Temp\ipykernel_16628\2085228624.py:1: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  corpus_embeddings = torch.tensor(corpus_embeddings)


In [64]:
d = DocContentManager()

In [65]:
def generateEmbeddings(docs):
    query_embeddings = []
    for i in docs:
        if i<7999999:
            query_embeddings.append(corpus_embeddings[i])
    return query_embeddings

# KeyBERT - Query Expansion and Keyword Generation

In [66]:
def expandQueryByKeyBert(query, passage_list, k=5):
    all_passages = " ".join(passage_list)
    keywords = kw_model.extract_keywords(all_passages, stop_words=query.split() ,top_n=k)
    new_user_query =  " ".join([term for term, _ in keywords]) + query
    return new_user_query

In [67]:
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize

# Function to extract keywords from a single query
def extract_keywords_from_query(query):
    # Tokenize the query
    words = word_tokenize(query)
    # Convert to lower case
    words = [word.lower() for word in words]
    # Remove stopwords
    stop_words = set(stopwords.words('english'))
    keywords = [word for word in words if word not in stop_words and word.isalnum()]
    return keywords

In [68]:
def findKeywords(query):
    k = len(query.split()) - 1
    keywords = kw_model.extract_keywords(query, top_n=k)
    new_user_query =  " ".join([term for term, _ in keywords])
    return new_user_query


# BM25

In [69]:
def executeBM25(query):

    relevant_docs = []

    query = extract_keywords_from_query(query)
    query = " ".join(query) 
    while True:
        cpp_executable_path = './bm25' 
        command = [cpp_executable_path, query]
        process = subprocess.run(command, capture_output=True, text=True)
        
        if process.returncode == 0:
            output_lines = process.stdout.strip().split('\n')

            # Process each line of output
            for line in output_lines:
                if line == "Word not found in index map." or line == "":
                    # print("New word - not found in corpus")
                    continue
                else:
                    pid = int(line)
                    if pid < 7999999: 
                        relevant_docs.append(pid)
        else:
            print("Error:", process.stderr)
        if len(relevant_docs) == 0 and len(query)>0:
            query = findKeywords(query)
        else:
            return relevant_docs
    

# Vocabulary Feedback


In [ ]:
def vocabularyFeedback(query, relevant_docs):
    passage_content = ""
    for pid in relevant_docs:
        passage_content += d.fetchPassageContent(pid) + " "
    keywords = kw_model.extract_keywords(passage_content, top_n=5)
    new_user_query =  query + " " + " ".join([term for term, _ in keywords])
    return new_user_query

# Semantic Search

In [76]:
def semantic_search(input_question, k=100):
    final_passages = []
    # print(input_question, " in semantic_search()")
    relevant_docs = executeBM25(input_question)
    print(vocabularyFeedback(input_question, relevant_docs))
    break
    # print(relevant_docs)
    relevant_embeddings = generateEmbeddings(relevant_docs)
    hits = util.semantic_search(relevant_embeddings, corpus_embeddings, top_k=k)
    for hit in hits[0]:
        final_passages.append(int(hit['corpus_id']))
    
    return final_passages

In [77]:
result = semantic_search("animals cages")

'''
for pid in result:
    print(str(pid)+" : ")
    print(d.fetchPassageContent(pid))
    print()
'''

animals cageszoo zoos zookeeper cages animals
4061138 : 
More than two decades ago I realized the common thread in the network of animal cruelty â the cage. The cage represents the imprisonment and mistreatment of the animals of this world. I have focused my career on tearing down these cages in their many forms and uses.

4061136 : 
Animals are being hurt in zoos not being taken care of because the chemicals in the cages of the animals can hurt them. Also they get little exercise which makes them weak and fat, and sometimes they get bored because they have nothing to do in their cages but just and eat and walk around.

4061133 : 
It is cruel to keep them in cages and They need the right to be free and fun around them.Animals should take their time to get used to the fact that they live in the wild and the habits of their kind.That is why I think That they should n'y be in cages.

4061135 : 
Zoos do more harm than good. Animals are being hurt in zoos not being taken care of because t

# Nearest Neighbour Search

In [9]:
nn_model = NearestNeighbors(n_neighbors=100, metric='euclidean')
nn_model.fit(corpus_embeddings)

NearestNeighbors(metric='euclidean', n_neighbors=100)

In [12]:
def nearestNeighbourSearch(input_question, k=100):
    relevant_docs = executeBM25(input_question)
    relevant_embeddings = []
    for doc in relevant_docs:
        content = d.fetchPassageContent(doc)
        user_query_embedding = sentence_transformer_model.encode([content])[0]
        relevant_embeddings.append(user_query_embedding)
    distances, indices = nn_model.kneighbors(relevant_embeddings, n_neighbors=k)
    return indices[0]


In [ ]:
result = nearestNeighbourSearch("animals cages")
for pid in result:
    print(str(pid)+" : ")
    print(d.fetchPassageContent(pid))
    print()

# Evaluating Semantic Search

In [91]:
import pandas as pd

queries = pd.read_csv(queries_path, delimiter='\t', header=None, names=['qid', 'query'])
top100 = pd.read_csv(top100_path, delimiter='\t', header=None, names=['qid', 'pid', 'query', 'passage'])
qrels = pd.read_csv(qrels_path, delimiter=' ', header=None, names=['qid', 'Q0', 'docid', 'rating'])


In [89]:
def evaluate_semantic_search():
    precision_scores = []
    recall_scores = []
    f1_scores = []

    for qid, group in top100.groupby('qid'):
        query = group['query'].tolist()[0]
        # print(query)

        relevant_documents = {x + 1 for x in set(group['pid'].tolist()) if x + 1 < 7999999}

        retrived_docs = semantic_search(query, 1000)

        retrieved_documents = set(retrived_docs)
        # print(relevant_documents)
        # print(retrieved_documents)

        diversity = diversity_at_k(relevant_documents, retrived_docs[:10])
        print(diversity)

        true_positive = len(retrieved_documents.intersection(relevant_documents))
        false_positive = len(retrieved_documents - relevant_documents)
        false_negative = len(relevant_documents - retrieved_documents)

        precision = true_positive / (true_positive + false_positive) if (true_positive + false_positive) > 0 else 0
        recall = true_positive / (true_positive + false_negative) if (true_positive + false_negative) > 0 else 0
        f1 = 2 * (precision * recall) / (precision + recall) if (precision + recall) > 0 else 0
        # print(precision, recall, f1)
        precision_scores.append(precision)
        recall_scores.append(recall)
        f1_scores.append(f1)
        # print(true_positive, false_positive, false_negative)

    average_precision = sum(precision_scores) / len(precision_scores)
    average_recall = sum(recall_scores) / len(recall_scores)
    average_f1 = sum(f1_scores) / len(f1_scores)

    print("Average Precision:", average_precision)
    print("Average Recall:", average_recall)
    print("Average F1 Score:", average_f1)

evaluate_semantic_search()


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

[3489331]
0.9816580528563298


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


[3683653]
0.9817519825296163


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


...

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


[6973593, 6973590, 6973592]
0.9817415042754182


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


[7666831, 2986227, 123547, 6484575, 6774305, 4786305, 5197130, 7112968, 7112964, 7057928, 742425, 6969187, 1059517, 3914970, 6685092, 3216315, 5758954, 2307979, 4689523]


KeyboardInterrupt: 

# Diversity@K

In [99]:
def diversity_at_k(top_k_documents):
    num_documents = len(top_k_documents)
    diversity_scores = []

    for i in range(num_documents):
        for j in range(i + 1, num_documents):
            embedding_i = corpus_embeddings[top_k_documents[i]]
            embedding_j = corpus_embeddings[top_k_documents[j]]
            similarity = cosine_similarity(embedding_i.reshape(1, -1), embedding_j.reshape(1, -1))[0, 0]
            diversity_scores.append(1 - similarity)

    diversity_at_k = sum(diversity_scores) / len(diversity_scores)
    return diversity_at_k



In [105]:
diversity_sum = 0

for index, query in queries.iterrows():
    print(query['query'])
    print()
    search_result = semantic_search(query['query'])
    diversity_score = diversity_at_k(search_result)
    diversity_sum+=diversity_score
    print(query, diversity_score)

print("Diversity@K average ", diversity_sum/len(queries))

what slows down the flow of blood



huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


qid                                1108939
query    what slows down the flow of blood
Name: 0, dtype: object 0.3796188066824518
what is the county for grand rapids, mn



huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


qid                                      1112389
query    what is the county for grand rapids, mn
Name: 1, dtype: object 0.2956010374276325
what is ruclip



huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

KeyboardInterrupt: 